In [1]:
### Checking for the GPU configuration
!nvidia-smi

Tue Feb 13 08:53:36 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 535.104.05             Driver Version: 535.104.05   CUDA Version: 12.2     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  Tesla T4                       Off | 00000000:00:04.0 Off |                    0 |
| N/A   41C    P8               9W /  70W |      0MiB / 15360MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

In [31]:
### Installing required libraries
!pip install wikipedia openai langchain faiss-cpu tiktoken sentence-transformers gradio

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.8/16.8 MB 47.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 92.1/92.1 kB 12.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 307.7/307.7 kB 35.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 138.7/138.7 kB 17.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.6/7.6 MB 61.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.8/60.8 kB 9.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 129.9/129.9 kB 20.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 71.5/71.5 kB 10.8 MB/s eta 0:00:00
  Created wheel for ffmpy: filename=ffmpy-0.3.2-py3-none-any.whl size=5584 sha256=be63c1e7ff9a275b153d378f8b52d277d8f5afa351b63a73c113b4300abe9f01
  Stored in directory: /root/.cache/pip/wheels/bd/65/9a/671fc6dcde07d4418df0c592f8df512b26d7a0029c2a23dd81
Successfully built ffmpy
ERROR: pip's dependency resol

### Designing the RAG Model

In [3]:
### importing libraries
import wikipedia
import pandas as pd
from tqdm import tqdm

In [4]:
### reading names of the players in the data and displaying few of them
players = pd.read_csv("/content/World's best top 35 footballers.csv", encoding = "latin-1")["Name"].to_list()
print("List of top 5 players : ", players[:5])

List of top 5 players :  ['Lionel Messi', 'Cristiano Ronaldo', 'Xavi Hernández', 'Andres Iniesta', 'Zlatan Ibrahimovic']


In [5]:
### extracting information about the players from their wikipedia pages
content = ""
for player in tqdm(players, desc = "Fetching Data : "):
  text = wikipedia.page(player, auto_suggest = False).content
  content += player.upper() + text + "\n"

Fetching Data : 100%|██████████| 35/35 [00:29<00:00,  1.20it/s]


In [6]:
### displaying the fetched data
display(content)

'LIONEL MESSILionel Andrés "Leo" Messi (Spanish pronunciation: [ljoˈnel anˈdɾes ˈmesi] ; born 24 June 1987) is an Argentine professional footballer who plays as a forward for and captains both Major League Soccer club Inter Miami and the Argentina national team. Widely regarded as one of the greatest players of all time, Messi has won a record eight Ballon d\'Or awards, a record six European Golden Shoes, and  was named the world\'s best player for a record eight times by FIFA. Until leaving the club in 2021, he had spent his entire professional career with Barcelona, where he won a club-record 34 trophies, including ten La Liga titles, seven Copa del Rey titles, and the UEFA Champions League four times. With his country, he won the 2021 Copa América and the 2022 FIFA World Cup. A prolific goalscorer and creative playmaker, Messi holds the records for most goals in La Liga (474), most hat-tricks in La Liga (36) and the UEFA Champions League (eight), and most assists in La Liga (192) an

In [7]:
### importing langchain modules for setting up the FAISS vectorstore
from langchain.text_splitter import CharacterTextSplitter
from langchain.vectorstores import FAISS
from langchain.embeddings import HuggingFaceEmbeddings

In [8]:
### configuring the embedding function for the text chunks
model_name = "sentence-transformers/all-mpnet-base-v2"
embeddings = HuggingFaceEmbeddings(model_name = model_name)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.6k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/363 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/239 [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

In [10]:
### splitting the text into text chunks before storing into the vectorstore
### keeping chunksize as 750, as the chosen embeddings can only return the max vector length of 768 chunks
from langchain.text_splitter import RecursiveCharacterTextSplitter
text_splitter = RecursiveCharacterTextSplitter(
    separators = [".", "\n"],
    chunk_size = 750,
    chunk_overlap = 125,
    length_function = len
)

### storing the text chunks into the vectorstore
documents = text_splitter.split_text(content)
vectorstore = FAISS.from_texts(documents, embeddings)

### saving the FAISS vectorstore
vectorstore.save_local("FAISS-Vectorstore")

In [13]:
### testing out the vectorstore for a search query
query_text = "Who is Cristiano Ronaldo?"
result = vectorstore.similarity_search_with_relevance_scores(query_text, k = 4)
display(result)

[(Document(page_content=".\nOne of the world's most marketable and famous athletes, Ronaldo was ranked the world's highest-paid athlete by Forbes in 2016, 2017, and 2023, and the world's most famous athlete by ESPN from 2016 to 2019. Time included him on their list of the 100 most influential people in the world in 2014. He is the first footballer and the third sportsman to earn US$1 billion in his career.\n\n\n== Early life ==\nCristiano Ronaldo dos Santos Aveiro was born on 5 February 1985 in the São Pedro parish of Funchal, the capital of the Portuguese island of Madeira, and grew up in the nearby parish of Santo António"),
  0.49410109349270226),
 (Document(page_content='." While stating they were stylistically different players who shared an equal desire to score goals, former Brazil international Ronaldo praised Cristiano\'s approach to training, arguing that "there are so few players who take care of their body like he does. I trained because I had to, he does it because he love

In [14]:
### creating a prompt template to give input to the llm in a desired format
from langchain.prompts import PromptTemplate

PROMPT_TEMPLATE = """
Consider yourself to be a football expert who has been given the task to answer a question
based on some of the content you are provided with along with their some relevance scores.
Please restrict your knowledge to only the given content and do not add up anything on your own.
Also make sure that if the top relevance score is less than 0.25, generate a response that you weren't able
to find anything relevant from the knowledge base.

Here's the question which you have been asked :
{question}

Here's the content you are provided with :
{content}

Here's the maximum relevance score :
{score}
"""

content = "\n-----\n".join([x[0].page_content for x in result])
score = max([x[1] for x in result])

prompt = PromptTemplate.from_template(PROMPT_TEMPLATE)
prompt = prompt.format(question = query_text, content = content, score = score)

In [20]:
### Initialising the OpenAI llm for generating the response based on the given input query and content
from langchain.llms import OpenAI
llm = OpenAI(temperature = 0.95)

response = llm.predict(prompt).strip()
display(response)

"Cristiano Ronaldo is a famous athlete who was born in Funchal, Portugal in 1985. He is known for his exceptional skills on the football field and has been ranked as the world's highest-paid athlete and most famous athlete in previous years. His determination to succeed and his love for training have made him one of the greatest footballers of all time. He is also credited with inspiring the success of Portuguese football in recent years."

In [29]:
### creating a generate_response function to take the input query and show the output
def generate_response(input_query):
  result = vectorstore.similarity_search_with_relevance_scores(input_query, k = 4)
  PROMPT_TEMPLATE = """
  Consider yourself to be a football expert who has been given the task to answer a question
  based on some of the content you are provided with along with their some relevance scores.
  Please restrict your knowledge to only the given content and do not add up anything on your own.
  Also make sure that if the top relevance score is less than 0.25, generate a response that you weren't able
  to find anything relevant from the knowledge base.

  Here's the question which you have been asked :
  {question}

  Here's the content you are provided with :
  {content}

  Here's the maximum relevance score :
  {score}
  """

  content = "\n-----\n".join([x[0].page_content for x in result])
  score = max([x[1] for x in result])

  prompt = PromptTemplate.from_template(PROMPT_TEMPLATE)
  prompt = prompt.format(question = input_query, content = content, score = score)

  llm = OpenAI(temperature = 0.95)
  response = llm.predict(prompt).strip()

  return response

In [30]:
### Testing the function
generate_response("Tell me some details about Pirlo")

"Pirlo is considered one of the best passers in the history of football, and is known for his accurate striking ability. He is also a free-kick and penalty-kick specialist, making him a valuable asset to his team's offensive play with goals and assists. Pirlo started his career in a more advanced role as an attacking midfielder and supporting striker, but was later moved to a deep-lying playmaker role where he excelled due to his unique capabilities. He was elected into the Italian Football Hall of Fame in 2019 and has since retired from playing to pursue coaching. In his debut season as coach, he won the Coppa Italia and Supercoppa Italiana before being dismissed in 2021."

### Designing the User Interface with Gradio

In [ ]:
### creating and launching the interface
import gradio as gr

interface = gr.Interface(fn = generate_response, inputs = gr.Textbox(), outputs = gr.Text())
interface.launch()